In [ ]:
# get markers?

In [2]:
library(Seurat)
library(dplyr)
library(SingleCellExperiment)
library(MetaMarkers)

In [3]:
sc1 = readRDS('overall_heart.rds')
sc1

An object of class Seurat 
33538 features across 142946 samples within 1 assay 
Active assay: RNA (33538 features, 3000 variable features)
 3 layers present: counts, data, scale.data
 2 dimensional reductions calculated: pca, umap

In [4]:
mtd = sc1@meta.data
exp1 = LayerData(sc1, assay = 'RNA', layer = 'counts')
mtd[1:2,]

orig.ident nCount_RNA nFeature_RNA percent.mt Rep Age
13W3D_LA_AAACCTGCAAACTGTC 13W3D_LA   16411      3984         1.602584   1   13 
13W3D_LA_AAACCTGCAAGGGTCA 13W3D_LA    9148      2934         4.667687   1   13 
                          Region RNA_snn_res.0.8 seurat_clusters clusters
13W3D_LA_AAACCTGCAAACTGTC LA     6               6               17      
13W3D_LA_AAACCTGCAAGGGTCA LA     14              14              31      
                          colors  major_cell_class
13W3D_LA_AAACCTGCAAACTGTC #00BA38 Fibro           
13W3D_LA_AAACCTGCAAGGGTCA #F564E3 WBC

In [5]:
table(mtd$major_cell_class)


      P-RBC         WBC         LEC         BEC Endocardial    Neuronal 
        346        4935         533        5100        6377        2403 
 Epicardial       Fibro         SMC        ncCM         aCM         vCM 
        888       55852       10894        2704       20268       32646 

In [6]:
# get SCE object
sce2 = SingleCellExperiment(list(counts = exp1), colData = DataFrame(mtd))
assay(sce2, "cpm") = convert_to_cpm(assay(sce2))

In [7]:
# get cell type markers on whole data
markers = compute_markers(assay(sce2, "cpm"), cell_type_labels = sce2$major_cell_class)
head(markers)

group cell_type gene   fold_change auroc     log_fdr   population_size
1 all   BEC       GNG11  10.965938   0.9873623 -7008.238 5100           
2 all   BEC       CDH5   50.122962   0.9739515 -6627.867 5100           
3 all   BEC       CAV1   10.530477   0.9728690 -6597.628 5100           
4 all   BEC       TMSB10  3.451981   0.9670054 -6435.031 5100           
5 all   BEC       RAMP2   9.866878   0.9647507 -6373.048 5100           
6 all   BEC       CALM1   6.144303   0.9643288 -6361.483 5100           
  population_fraction average_expression se_expression detection_rate
1 0.03567781           2572.1090         16.924471     0.9976471     
2 0.03567781            548.6213          4.868394     0.9611765     
3 0.03567781           2192.9212         18.234901     0.9915686     
4 0.03567781          12669.7690         70.901392     1.0000000     
5 0.03567781           1704.6644         12.411526     0.9931373     
6 0.03567781           2419.7458         18.938767     0.9980392     
  fold_change_detection precision  recall   
1  1.612451             0.05633117 0.9976471
2 19.766799             0.42722677 0.9611765
3  1.689076             0.05885502 0.9915686
4  1.004060             0.03581763 1.0000000
5  2.410777             0.08199641 0.9931373
6  1.184033             0.04197557 0.9980392

In [8]:
head(markers[markers$cell_type=='vCM',])

group cell_type gene   fold_change auroc     log_fdr   population_size
1 all   vCM       MYH7    85.407105  0.9930799 -36742.53 32646          
2 all   vCM       MYL2   110.808955  0.9865765 -35779.77 32646          
3 all   vCM       MYL3    30.231564  0.9820284 -35114.14 32646          
4 all   vCM       SORBS2   8.642862  0.9588895 -31823.92 32646          
5 all   vCM       TNNI1    6.649490  0.9571412 -31581.98 32646          
6 all   vCM       FABP3    8.204410  0.9479996 -30331.50 32646          
  population_fraction average_expression se_expression detection_rate
1 0.2283799           6218.914           16.980985     0.9922196     
2 0.2283799           6608.894           33.270158     0.9833977     
3 0.2283799           6595.006           17.193620     0.9884519     
4 0.2283799           1583.793            5.039416     0.9963855     
5 0.2283799           4999.709            9.089921     0.9997243     
6 0.2283799           1427.641            4.104850     0.9880843     
  fold_change_detection precision recall   
1 5.384905              0.6155132 0.9922196
2 6.387642              0.6552907 0.9833977
3 3.201114              0.4870645 0.9884519
4 2.664474              0.4413209 0.9963855
5 2.271364              0.4023150 0.9997243
6 3.297217              0.4944814 0.9880843

In [9]:
# save marker list
export_meta_markers(markers, "Farah_celltype_markers.csv", names(markers))